#  HDiv-HDG for Stokes equations

Consider the Stokes equations

$$
\begin{aligned}
-2\mu\nabla\cdot\epsilon(u)+\nabla p = &\; f,\\
\nabla \cdot u = &\; 0
\end{aligned}
$$

Deformation tensor: $\epsilon(u)=0.5(\nabla u+\nabla u^T)$. 
Domain $\Omega$:
<img src="domain_cyl.png" alt="Drawing" style="width: 400px;"/>
Boundary conditions:
$$
\left\{
\begin{aligned}
u = u_{in}&\quad \text{ on }\Gamma_{inlet}\\[.3ex]
u=0&\quad \text{ on }\Gamma_{wall}\cup \Gamma_{cyl}\\[.3ex]
\left[2\mu\epsilon(u)-p\mathbf{I}\right]n = 0&\quad \text{ on }\Gamma_{outlet}\\[.3ex]
\end{aligned}
\right.
$$
Inflow velocity $u_{in} = \left(\frac{4Uy(0.41-y)}{0.41^2}, 0\right)$ with $U=1.5$. 
No source $f=0$. Viscosity $\mu = 0.001$.

Define channel geometry and mesh it:

In [1]:
from ngsolve import *
from ngsolve.webgui import Draw

from netgen.geom2d import SplineGeometry
geo = SplineGeometry()
geo.AddRectangle( (0, 0), (2, 0.41), bcs = ("wall", "outlet", "wall", "inlet"))
geo.AddCircle ( (0.2, 0.2), r=0.05, leftdomain=0, rightdomain=1, bc="cyl")
mesh = Mesh( geo.GenerateMesh(maxh=0.05))
mesh.Curve(3)
Draw(mesh)

NGSWebGuiWidget(value={'ngsolve_version': '6.2.2005-14-g40518403', 'mesh_dim': 2, 'order2d': 2, 'order3d': 2, …

Use mixed finite element pairing from Darcy flow

In [2]:
V = HDiv(mesh, order=1, dirichlet="wall|inlet|cyl") # HDiv space BDM-P1
VF = TangentialFacetFESpace(mesh, order=1, dirichlet="wall|inlet|cyl") # tangential facet fespace on skeleton
Q = L2(mesh, order=0)
fes = FESpace([V,VF, Q]) # NO dgjumps flag: more total dofs but less dofs coupling

Setup bilinear-form for Stokes.

In [3]:
(u,uhat, p), (v, vhat, q) = fes.TnT()

alpha = 4 # stablization paramter = alpha r^2/h
k = 1 # velocity poly degree is 1
h = specialcf.mesh_size
n = specialcf.normal(mesh.dim)

mu = 0.001
epsu = 0.5*(grad(u)+grad(u).trans)
epsv = 0.5*(grad(v)+grad(v).trans)

def tang(v): # the tangential component of a vector
    return v-(v*n)*n

jmp_u = tang(u-uhat)
jmp_v = tang(v-vhat)

# boundary terms
vis_INT =  2*mu*(-epsu*n*jmp_v-epsv*n*jmp_u + alpha*k**2/h*jmp_u*jmp_v)

a = BilinearForm(fes)
# epsu and epsv are second-order tensors, use InnerProduct
a += (2*mu*InnerProduct(epsu, epsv) - div(u)*q - div(v)*p) * dx
a += vis_INT*dx(element_boundary=True) # HDG ALWAYS USE ELEMENT_BOUNDARY FORMULATION
a.Assemble()

Set inhomogeneous Dirichlet boundary condition only on inlet boundary:

In [4]:
gfu = GridFunction(fes)
uh, uhath, ph = gfu.components
uin = CoefficientFunction((1.5*4*y*(0.41-y)/(0.41*0.41),0)) # a vector inflow
gfu.components[0].Set(uin, definedon=mesh.Boundaries("inlet"))
# tangential component has zero dirichelt data: do nothing

res = gfu.vec.CreateVector()
res.data = -a.mat * gfu.vec # Dirichelt BC treatment
inv = a.mat.Inverse(freedofs=fes.FreeDofs(), inverse="umfpack")
gfu.vec.data += inv * res
Draw(uh, mesh, "vel", min=0, max=2)

NGSWebGuiWidget(value={'ngsolve_version': '6.2.2005-14-g40518403', 'mesh_dim': 2, 'order2d': 2, 'order3d': 2, …

### Define the HDiv-HDG solver

In [5]:
def HDivHDGSolveStokes(fes, mu=0.001, vis=True, condense=False): # activatate static condensation
    # grid function
    gfu = GridFunction(fes)
    uh, uhath, ph = gfu.components
    
    (u,uhat, p), (v, vhat, q) = fes.TnT()

    alpha = 4 # stablization paramter = alpha r^2/h
    k = 1 # velocity poly degree is 1
    h = specialcf.mesh_size
    n = specialcf.normal(mesh.dim)

    mu = 0.001
    epsu = 0.5*(grad(u)+grad(u).trans)
    epsv = 0.5*(grad(v)+grad(v).trans)

    def tang(v): # the tangential component of a vector
        return v-(v*n)*n

    jmp_u = tang(u-uhat)
    jmp_v = tang(v-vhat)

    # boundary terms
    vis_INT =  2*mu*(-epsu*n*jmp_v-epsv*n*jmp_u + alpha*k**2/h*jmp_u*jmp_v)

    a = BilinearForm(fes, condense=condense)
    # epsu and epsv are second-order tensors, use InnerProduct
    # add a regularization term
    a += (2*mu*InnerProduct(epsu, epsv)- div(u)*q - div(v)*p) * dx
    a += vis_INT*dx(element_boundary=True) # HDG ALWAYS USE ELEMENT_BOUNDARY FORMULATION
    a.Assemble()
    
    uin = CoefficientFunction((1.5*4*y*(0.41-y)/(0.41*0.41),0)) # a vector inflow
    gfu.components[0].Set(uin, definedon=mesh.Boundaries("inlet"))

    # rhs and solve
    res = gfu.vec.CreateVector()
    res.data = -a.mat * gfu.vec # Dirichelt BC treatment
    if condense:
        res.data += a.harmonic_extension_trans * res
    inv = a.mat.Inverse(fes.FreeDofs(condense), "umfpack")
    gfu.vec.data += inv * res
    if condense:
        gfu.vec.data += a.harmonic_extension * gfu.vec
        gfu.vec.data += a.inner_solve * res

    # visualization of velocity
    if vis:
        Draw(uh, mesh, "vel", min=0, max=2)
    
    ndof_total = fes.ndof
    ndof_global = sum(fes.FreeDofs(True))
    ndof_local = ndof_total - ndof_global
    print("Local DOFs: %.2e, Global DOFs: %.2e" %(ndof_local, ndof_global))
    
    return gfu

### lowest order HDiv-DG on finer mesh

In [6]:
# test condensation:: FAIL

# change pressure constant DOFs --> INTERFACE DOFS
ndofV = V.ndof+VF.ndof
fes.FreeDofs(True)[ndofV:ndofV+mesh.ne] = True 

print(sum(fes.FreeDofs()))
print(sum(fes.FreeDofs(True)))

gfu = HDivHDGSolveStokes(fes, condense=True)

5248
5248


NgException: UmfpackInverse: Numeric factorization failed.

In [7]:
gfu = HDivHDGSolveStokes(fes, condense=False)

NGSWebGuiWidget(value={'ngsolve_version': '6.2.2005-14-g40518403', 'mesh_dim': 2, 'order2d': 2, 'order3d': 2, …

Local DOFs: 4.00e+02, Global DOFs: 5.25e+03
